In [2]:
import numpy as np
import cv2
import time 
import random
from keras.models import load_model

model = load_model(r'C:\Users\HP\Documents\PCV\Poker2.h5')
camera = cv2.VideoCapture(1)
camera.set(10, 500)

BKG_THRESH = 70

GAME_STATUS = "Playing"
WINNER = None
GameSelesai = False

card_min_area = 25000  
card_max_area = 45000  
Card = None
KartuTerdeteksi = []

NilaiKartu = {
    "2 Hearts": 2, "3 Hearts": 3, "4 Hearts": 4, "5 Hearts": 5, "6 Hearts": 6, "7 Hearts": 7, "8 Hearts": 8, "9 Hearts": 9, "10 Hearts": 10, 
    "Jack Hearts": 10, "Queen Hearts": 10, "King Hearts": 10, "Ace Hearts": 11, "2 Spades": 2, "3 Spades": 3, "4 Spades": 4, "5 Spades": 5, 
    "6 Spades" : 6, "7 Spades" : 7, "8 Spades" : 8, "9 Spades" : 9, "10 Spades" : 10, "Jack Spades" : 10, "Queen Spades" : 10, "King Spades" : 10, 
    "Ace Spades" : 11, "2 Diamonds" : 2, "3 Diamonds" : 3, "4 Diamonds" : 4, "5 Diamonds" : 5, "6 Diamonds" : 6, "7 Diamonds" : 7, "8 Diamonds" : 8,
    "9 Diamonds" : 9, "10 Diamonds" : 10, "Jack Diamonds" : 10, "Queen Diamonds" : 10, "King Diamonds" : 10, "Ace Diamonds" : 11, "2 Clubs" : 2, 
    "3 Clubs" : 3, "4 Clubs" : 4, "5 Clubs" : 5, "6 Clubs" : 6, "7 Clubs" : 7, "8 Clubs" : 8, "9 Clubs" : 9, "10 Clubs" : 10, "Jack Clubs" :10,
      "Queen Clubs" : 10, "King Clubs" : 10, "Ace Clubs" : 11
}

KartuTerdeteksi_left = []
KartuTerdeteksi_right = []
PemainAmbilKartu = False 
JumlahKartuPemain = 0
JumlahKartuKomputer = 0
detected_cards = set()

class Kartu:

     def __init__(self):
        self.contour = [] 
        self.width, self.height = 0, 0 
        self.corner_pts = [] 
        self.warp = [] 
def ProsesFrame(image):
    gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    blur = cv2.GaussianBlur(gray, (5, 5), 0)

    img_w, img_h = np.shape(image)[:2]
    bkg_level = gray[int(img_h/100)][int(img_w/2)]
    thresh_level = bkg_level + BKG_THRESH

    _, thresh = cv2.threshold(blur, thresh_level, 255, cv2.THRESH_BINARY)
    edges = cv2.Canny(blur, threshold1=50, threshold2=150)
    combined = cv2.bitwise_or(thresh, edges)

    return combined
def ProsesKartu(contour, image):

    Card = Kartu()
    Card.contour = contour

    # Find perimeter of card and use it to approximate corner points
    peri = cv2.arcLength(contour,True)
    approx = cv2.approxPolyDP(contour,0.01*peri,True)

    if len(approx) != 4:
        return None
    
    pts = np.float32(approx)
    Card.corner_pts = pts

    # Find width and height of card's bounding rectangle
    x,y,w,h = cv2.boundingRect(contour)
    Card.width, Card.height = w, h

    # Warp card into 200x300 flattened image using perspective transform
    Card.warp = flattener(image, pts, w, h)
    return Card

def flattener(image, pts, w, h):
    s = np.sum(pts, axis = 2)
    diff = np.diff(pts, axis = -1)
    rect = np.zeros((4, 2), dtype = "float32")

    rect[0] = pts[np.argmin(s)]        # Top-left point
    rect[2] = pts[np.argmax(s)]        # Bottom-right point
    rect[1] = pts[np.argmin(diff)]     # Top-right point
    rect[3] = pts[np.argmax(diff)]     # Bottom-left point

    # Perspective transformation
    maxWidth, maxHeight = 200, 300
    dst = np.array([[0, 0], [maxWidth - 1, 0], [maxWidth - 1, maxHeight - 1], [0, maxHeight - 1]], dtype="float32")
    M = cv2.getPerspectiveTransform(rect, dst)
    warp = cv2.warpPerspective(image, M, (maxWidth, maxHeight))
        

    return warp

def ProsesInputModel(image):
    processed_image = cv2.resize(image, (200, 300))
    # if len(processed_image.shape) == 2:  
    #     processed_image = cv2.cvtColor(processed_image, cv2.COLOR_GRAY2BGR)
        
    rgb = cv2.cvtColor(processed_image, cv2.COLOR_BGR2RGB)
    processed_image = np.asarray(rgb) / 255.0
    # processed_image = processed_image.astype('float32')
    return processed_image, rgb

def save_flattened_image(image, filename):
    if image is not None:
        cv2.imwrite(filename, image)

def DeteksiLeft(frame):
    global Card
    detected_cards_left = []
    FrameKiri = frame[:, :frame.shape[1]//2]
    combined_left = ProsesFrame(FrameKiri)
    contours, _ = cv2.findContours(combined_left, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

    for contour in contours:
        area = cv2.contourArea(contour)
        if card_min_area < area < card_max_area:
            
            cv2.drawContours(FrameKiri, [contour], 0, (255, 0, 0), 2)
            Card = ProsesKartu(contour, FrameKiri)
            
            if Card is not None:
                processed_card_image, rgb = ProsesInputModel(Card.warp)
                prediction = model.predict(np.expand_dims(processed_card_image, axis=0))
                predicted_class = np.argmax(prediction, axis=1)

                # cv2.imshow('Flattened', Card.warp)

                LabelKartu = [  "2 Hearts", "3 Hearts", "4 Hearts", "5 Hearts", "6 Hearts", "7 Hearts", "8 Hearts", "9 Hearts", "10 Hearts", "Jack Hearts", "Queen Hearts", "King Hearts", "Ace Hearts",
                                "2 Spades", "3 Spades", "4 Spades", "5 Spades", "6 Spades", "7 Spades", "8 Spades", "9 Spades", "10 Spades", "Jack Spades", "Queen Spades", "King Spades", "Ace Spades",
                                "2 Diamonds", "3 Diamonds", "4 Diamonds", "5 Diamonds", "6 Diamonds", "7 Diamonds", "8 Diamonds", "9 Diamonds", "10 Diamonds", "Jack Diamonds", "Queen Diamonds", "King Diamonds", "Ace Diamonds",
                                "2 Clubs", "3 Clubs", "4 Clubs", "5 Clubs", "6 Clubs", "7 Clubs", "8 Clubs", "9 Clubs", "10 Clubs", "Jack Clubs", "Queen Clubs", "King Clubs", "Ace Clubs"]
                LabelPred = LabelKartu[predicted_class[0]]
                card_value = NilaiKartu.get(LabelPred, 0)  
                detected_cards_left.append((LabelPred, card_value))

                x,y,w,h = cv2.boundingRect(contour)
                cv2.rectangle(frame,(x,y),(x+w, y+h),(0,255,0),2)
                cv2.putText(frame,LabelPred,(x,y-10),cv2.FONT_HERSHEY_SIMPLEX,0.5, (0,255,0),2)
    
    return FrameKiri, detected_cards_left

def DeteksiRight(frame):
    global Card
    detected_cards_right = []
    FrameKanan = frame[:, frame.shape[1]//2:]
    combined_right = ProsesFrame(FrameKanan)
    contours, _ = cv2.findContours(combined_right, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

    for contour in contours:
        area = cv2.contourArea(contour)
        if card_min_area < area < card_max_area:
            x,y,w,h = cv2.boundingRect(contour)
            x_adjusted = x + frame.shape[1]//2 
            cv2.drawContours(FrameKanan, [contour], 0, (255, 0, 0), 2)
            Card = ProsesKartu(contour, FrameKanan)
            
            if Card is not None:
                processed_card_image, rgb = ProsesInputModel(Card.warp)
                prediction = model.predict(np.expand_dims(processed_card_image, axis=0))
                predicted_class = np.argmax(prediction, axis=1)

                LabelKartu = [  "2 Hearts", "3 Hearts", "4 Hearts", "5 Hearts", "6 Hearts", "7 Hearts", "8 Hearts", "9 Hearts", "10 Hearts", "Jack Hearts", "Queen Hearts", "King Hearts", "Ace Hearts",
                                "2 Spades", "3 Spades", "4 Spades", "5 Spades", "6 Spades", "7 Spades", "8 Spades", "9 Spades", "10 Spades", "Jack Spades", "Queen Spades", "King Spades", "Ace Spades",
                                "2 Diamonds", "3 Diamonds", "4 Diamonds", "5 Diamonds", "6 Diamonds", "7 Diamonds", "8 Diamonds", "9 Diamonds", "10 Diamonds", "Jack Diamonds", "Queen Diamonds", "King Diamonds", "Ace Diamonds",
                                "2 Clubs", "3 Clubs", "4 Clubs", "5 Clubs", "6 Clubs", "7 Clubs", "8 Clubs", "9 Clubs", "10 Clubs", "Jack Clubs", "Queen Clubs", "King Clubs", "Ace Clubs"]
                LabelPred = LabelKartu[predicted_class[0]]
                card_value = NilaiKartu.get(LabelPred, 0)
                detected_cards_right.append((LabelPred, card_value))
                cv2.rectangle(frame, (x_adjusted, y), (x_adjusted + w, y + h), (0, 255, 0), 2)
                cv2.putText(frame, LabelPred, (x_adjusted, y - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (0, 255, 0), 2)

    return FrameKanan, detected_cards_right

def blackjack(JumlahKiri, JumlahKanan, game_status):
    winner = None
    if game_status == "Playing":
        if JumlahKiri == 21:
            winner = "Left Player Wins"
            game_status = "Finished"
        elif JumlahKanan == 21:
            winner = "Right Player Wins"
            game_status = "Finished"
        elif JumlahKiri > 21:
            winner = "Right Player Wins"
            game_status = "Finished"
        elif JumlahKanan > 21:
            winner = "Left Player Wins"
            game_status = "Finished"
        else:
            if JumlahKiri > JumlahKanan:
                winner = "Left Player Wins"
            elif JumlahKanan > JumlahKiri:
                winner = "Right Player Wins"
            else:
                winner = "It's a Tie"
                game_status = "Finished"
    
    return game_status, winner

def process_new_detection(card_class):
    if card_class in detected_cards:
        print(f"{card_class} already detected, ignoring...")
        return False  
    else:
        detected_cards.add(card_class)
        print(f"Detected new card: {card_class}")
        return True  
    
def Komputer_minta():
    global target_card
    target_card = random.choice(list(NilaiKartu.keys()))
    print(f"Computer requests: {target_card}")
Komputer_minta()

while camera.isOpened():
    ret, frame = camera.read()
    if not ret:
        continue
    
    FrameKiri, new_cards_left = DeteksiLeft(frame)
    FrameKanan, new_cards_right = DeteksiRight(frame)
    FrameKiri = cv2.resize(FrameKiri, (400, 600))
    FrameKanan = cv2.resize(FrameKanan, (400, 600))
    
    FrameGabungan = np.concatenate((FrameKiri, FrameKanan), axis=1)
    cv2.line(FrameGabungan, (FrameGabungan.shape[1]//2, 0), (FrameGabungan.shape[1]//2, FrameGabungan.shape[0]), (0, 255, 0), 2)

    left_text_position = (FrameGabungan.shape[1] // 4 - 100, FrameGabungan.shape[0] // 2)
    right_text_position = (3 * FrameGabungan.shape[1] // 4 - 100, FrameGabungan.shape[0] // 2)

    print("Detected Left Cards:", KartuTerdeteksi_left)
    print("Detected Right Cards:", KartuTerdeteksi_right)

    JumlahKiri = sum(value for _, value in KartuTerdeteksi_left)
    JumlahKanan = sum(value for _, value in KartuTerdeteksi_right)

    requested_card_text = f"Requested: {target_card}"
    cv2.putText(FrameGabungan, requested_card_text, (FrameGabungan.shape[1]//2 + 10, 20), cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0, 0, 255), 2)

    if len(KartuTerdeteksi_left) < 2:
        FrameKiri, new_cards_left = DeteksiLeft(frame)
        for card, value in new_cards_left:
            if process_new_detection(card):
                KartuTerdeteksi_left.append((card, value))
                JumlahKartuPemain += 1
    else:
        FrameKiri = frame[:, :frame.shape[1]//2] 

    if len(KartuTerdeteksi_right) < 2:
        FrameKanan, new_cards_right = DeteksiRight(frame)
        for card, value in new_cards_right:
            if process_new_detection(card):
                if card == target_card:
                    KartuTerdeteksi_right.append((card, value))
                    JumlahKartuKomputer += 1
                    Komputer_minta()
    else:
        FrameKanan = frame[:, frame.shape[1]//2:]

     
    x_offset = 10  # Reset x_offset for left side cards
    y_offset = 45
    for card, _ in KartuTerdeteksi_left:
        cv2.putText(FrameGabungan, card, (x_offset, y_offset), cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0, 255, 0), 2)
        x_offset += 150 
        cv2.putText(FrameGabungan, f"Total Left: {JumlahKiri}", (10, 70), cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0, 255, 0), 2)
    
    x_offset = FrameGabungan.shape[1]//2 + 10  
    y_offset = 45 
    for card, _ in KartuTerdeteksi_right:
        cv2.putText(FrameGabungan, card, (x_offset, y_offset), cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0, 255, 0), 2)
        x_offset += 150  
        cv2.putText(FrameGabungan, f"Total Right: {JumlahKanan}", (FrameGabungan.shape[1]//2 + 10, 70), cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0, 255, 0), 2)

    cv2.putText(FrameGabungan, f"Game Status: {GAME_STATUS}", (10, 90), cv2.FONT_HERSHEY_SIMPLEX, 0.7, (0, 255, 0), 2)

    print("Total Left Value:", JumlahKiri)
    print("Total Right Value:", JumlahKanan)

    if len(KartuTerdeteksi_left) == 2 and len(KartuTerdeteksi_right) == 2:
        if GAME_STATUS == "Playing":
            GAME_STATUS, WINNER = blackjack(JumlahKiri, JumlahKanan, GAME_STATUS)    
        print("Game Status:", GAME_STATUS)
        print("Winner:", WINNER)
        if WINNER:
            GameSelesai = True

        if GameSelesai == True:
            if WINNER == "Left Player Wins":
                cv2.putText(FrameGabungan, "Winner", left_text_position, cv2.FONT_HERSHEY_SIMPLEX, 1.0, (0, 255, 0), 3)
                cv2.putText(FrameGabungan, "Loser", right_text_position, cv2.FONT_HERSHEY_SIMPLEX, 1.0, (0, 0, 255), 3)
            else:
                cv2.putText(FrameGabungan, "Loser", left_text_position, cv2.FONT_HERSHEY_SIMPLEX, 1.0, (0, 0, 255), 3)
                cv2.putText(FrameGabungan, "Winner", right_text_position, cv2.FONT_HERSHEY_SIMPLEX, 1.0, (0, 255, 0), 3)

    key = cv2.waitKey(1) & 0xFF
    if key == ord('q'):
        break
    elif key == ord('f'): 
        if Card is not None and Card.warp is not None:
            timestamp = time.strftime("%Y%m%d-%H%M%S")
            save_flattened_image(Card.warp, f"flattened_image_{timestamp}.png")
    elif key == ord('r'):
        KartuTerdeteksi_left.clear()
        KartuTerdeteksi_right.clear()
        detected_cards.clear() 
        GAME_STATUS = "Playing"
        WINNER = None
        GameSelesai = False
        JumlahKartuPemain = 0 
        JumlahKartuKomputer = 0
        Komputer_minta()
    elif key == ord('a'): 
        KartuTerdeteksi_left.extend(new_cards_left)
        PemainAmbilKartu = True
        JumlahKartuPemain += len(new_cards_left)
    cv2.imshow('Deteksi Kartu', FrameGabungan)
camera.release()
cv2.destroyAllWindows()



Computer requests: 9 Diamonds
Detected Left Cards: []
Detected Right Cards: []
Total Left Value: 0
Total Right Value: 0
Detected Left Cards: []
Detected Right Cards: []
Total Left Value: 0
Total Right Value: 0
Detected Left Cards: []
Detected Right Cards: []
Total Left Value: 0
Total Right Value: 0
Detected Left Cards: []
Detected Right Cards: []
Total Left Value: 0
Total Right Value: 0
Detected Left Cards: []
Detected Right Cards: []
Total Left Value: 0
Total Right Value: 0
Detected Left Cards: []
Detected Right Cards: []
Total Left Value: 0
Total Right Value: 0
Detected Left Cards: []
Detected Right Cards: []
Total Left Value: 0
Total Right Value: 0
Detected Left Cards: []
Detected Right Cards: []
Total Left Value: 0
Total Right Value: 0
Detected Left Cards: []
Detected Right Cards: []
Total Left Value: 0
Total Right Value: 0
Detected Left Cards: []
Detected Right Cards: []
Total Left Value: 0
Total Right Value: 0
Detected Left Cards: []
Detected Right Cards: []
Total Left Value: 0
T